# Fine-tune FLAN-T5 using `bitsandbytes`, `peft` & `transformers` 🤗

In this notebook we will see how to properly use `peft` , `transformers` & `bitsandbytes` to fine-tune `flan-t5-large` in a google colab!

We will finetune the model on [`financial_phrasebank`](https://huggingface.co./datasets/financial_phrasebank) dataset, that consists of pairs of text-labels to classify financial-related sentences, if they are either `positive`, `neutral` or `negative`.

Note that you could use the same notebook to fine-tune `flan-t5-xl` as well, but you would need to shard the models first to avoid CPU RAM issues on Google Colab, check [these weights](https://huggingface.co./ybelkada/flan-t5-xl-sharded-bf16).

## TODO #1

`google/flan-t5-large` 모델은 무엇을 목표로 만들어졌고 기대할 수 있는 기능은 무엇인지 조사하시오
- 마크다운 스타일로 작성하시오

## 'google/flan-t5-large' 모델 개요

- 'google/flan-t5-large' 모델은 T5 아키텍처를 기반으로 합니다.
- T5 모델은 텍스트 입력을 받아 출력을 생성하는 시퀀스 투 시퀀스 모델로, NLP 작업을 수행하는 데 사용됩니다.
- 이 모델은 "모든 것은 텍스트"라는 접근을 따르며 입력 텍스트와 출력 텍스트를 동일한 형식으로 처리합니다.

## 기대 기능과 활용

- 'google/flan-t5-large' 모델은 다음과 같은 다양한 NLP 작업을 수행할 수 있습니다:
  - 텍스트 생성: 입력 텍스트로부터 다양한 종류의 텍스트를 생성합니다.
  - 요약: 긴 문서나 텍스트를 간결한 요약으로 변환합니다.
  - 번역: 다국어 번역 작업을 수행하며 입력 텍스트를 다른 언어로 번역합니다.
  - 질문 응답: 질문에 대한 답변을 생성하고, 지문과 질문을 이해하여 답변합니다.
  - 문장 분류: 주어진 문장을 카테고리 또는 클래스로 분류합니다.

'google/flan-t5-large' 모델을 통해 다양한 NLP 작업을 자동화하고 향상시키기 위해, 모델의 특정 기능과 작업에 따른 설정 및 데이터가 필요하며, 이를 통해 정확하고 효율적인 자연어 처리 작업을 수행할 수 있습니다.

## Install requirements

In [ ]:
!pip install -q bitsandbytes datasets accelerate
!pip install -q git+https://github.com/huggingface/transformers.git@main git+https://github.com/huggingface/peft.git@main

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


## Import model and tokenizer

In [ ]:
# Select CUDA device index
import os
import torch

os.environ["CUDA_VISIBLE_DEVICES"] = "0"

from datasets import load_dataset
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

model_name = "google/flan-t5-large"

model = AutoModelForSeq2SeqLM.from_pretrained(model_name, load_in_8bit=True)
tokenizer = AutoTokenizer.from_pretrained(model_name)

## Prepare model for training

Some pre-processing needs to be done before training such an int8 model using `peft`, therefore let's import an utiliy function `prepare_model_for_int8_training` that will:
- Casts all the non `int8` modules to full precision (`fp32`) for stability
- Add a `forward_hook` to the input embedding layer to enable gradient computation of the input hidden states
- Enable gradient checkpointing for more memory-efficient training

In [ ]:
from peft import prepare_model_for_int8_training

model = prepare_model_for_int8_training(model)

## Load your `PeftModel`

Here we will use LoRA (Low-Rank Adaptators) to train our model

In [ ]:
from peft import LoraConfig, get_peft_model, TaskType


def print_trainable_parameters(model):
    """
    Prints the number of trainable parameters in the model.
    """
    trainable_params = 0
    all_param = 0
    for _, param in model.named_parameters():
        all_param += param.numel()
        if param.requires_grad:
            trainable_params += param.numel()
    print(
        f"trainable params: {trainable_params} || all params: {all_param} || trainable%: {100 * trainable_params / all_param}"
    )


lora_config = LoraConfig(
    r=16, lora_alpha=32, target_modules=["q", "v"], lora_dropout=0.05, bias="none", task_type="SEQ_2_SEQ_LM"
)


model = get_peft_model(model, lora_config)
print_trainable_parameters(model)

As you can see, here we are only training 0.6% of the parameters of the model! This is a huge memory gain that will enable us to fine-tune the model without any memory issue.

## TODO #2

위와 같이 0.6%로 학습 파라미터의 갯수가 대폭 축소된 원리에 대해 개략적으로 조사하시오.
- 마크다운 스타일로 작성하시오

## 모델 파라미터 크기 축소 및 메모리 효율성 개선

제공된 코드에서 사용된 기술은 모델 파라미터의 크기를 축소하면서 메모리 효율성을 개선하고 모델을 학습 가능한 상태로 유지하는 방법입니다. 이 기술은 메모리 제약이 있는 환경에서 효과적으로 모델을 활용하는 데 도움을 줍니다.

- **모델 파라미터 출력 및 메모리 이득**:
  - `print_trainable_parameters` 함수는 모델의 학습 가능한 파라미터 수를 출력합니다.
  - 결과에서 "trainable params"는 실제로 학습 가능한 파라미터 수를 나타냅니다.
  - "all params"는 모델의 총 파라미터 수를 나타냅니다.
  - "trainable%"은 학습 가능한 파라미터의 백분율을 나타냅니다.
  - 결과에서 "trainable%"가 매우 낮게 나타나면, 모델 파라미터 중 일부만이 학습 가능한 상태로 유지되고, 메모리 요구 사항이 크게 줄어들게 됩니다.

이 접근 방식은 메모리 제약이 있는 환경에서 큰 모델을 미세 조정하고자 할 때 효과적이며, 메모리를 효율적으로 활용할 수 있게 해줍니다. 또한 모델을 효율적으로 학습하고 사용할 수 있도록 도와줍니다.

## TODO #3

모델 로드시 `load_in_8bit=True` 옵션을 사용하지 않으면 원본을 로딩한다.

이 때의 모델 구조와,  `load_in_8bit=True` 을 사용했을 때의 무델 구조를 비교하여 어떤 차이점이 있는지를 조사하시오.
- 마크다운 스타일로 작성하시오

## `load_in_8bit=True`와 `load_in_8bit=False` 모델 로드 옵션 비교

`load_in_8bit=True` 옵션을 사용하여 모델을 로드하는 경우와 그렇지 않은 경우 모델 구조에 차이가 있을 수 있으며, 주요 차이점은 다음과 같습니다:

1. **모델 파라미터의 데이터 유형**:
   - `load_in_8bit=True`를 사용한 경우: 모델 파라미터는 8비트 정밀도로 저장됩니다. 이는 모델의 가중치와 편향을 표현하는데 사용되는 숫자가 상대적으로 작음을 의미하며, 이는 모델이 메모리를 적게 사용하는 장점을 제공합니다.
   - `load_in_8bit=True`를 사용하지 않은 경우: 모델 파라미터는 일반적으로 32비트 또는 16비트로 저장됩니다. 이는 모델의 가중치와 편향이 상대적으로 큰 숫자를 가질 수 있으며, 이로 인해 메모리 요구 사항이 증가할 수 있습니다.

2. **모델 메모리 요구 사항**:
   - `load_in_8bit=True`를 사용한 경우: 모델이 사용하는 메모리 양이 감소하므로 더 효율적으로 작동할 수 있습니다.
   - `load_in_8bit=True`를 사용하지 않은 경우: 모델이 사용하는 메모리 양이 증가할 수 있습니다.

3. **성능 및 정확도**:
   - `load_in_8bit=True`를 사용한 경우: 모델 파라미터의 8비트 정밀도로 인해 모델의 성능과 정확도가 감소할 수도 있습니다. 이로 인해 예측의 정확도가 저하될 수 있습니다.
   - `load_in_8bit=True`를 사용하지 않은 경우: 원본 정밀도로 모델 파라미터가 로드되므로 모델의 성능이 더 높을 수 있습니다.

따라서 `load_in_8bit=True`를 사용하면 메모리 효율성이 개선되지만, 모델의 성능이 감소할 수 있으므로 적당하게 고려해서 사용해야 합니다.

## Load and process data

Here we will use [`financial_phrasebank`](https://huggingface.co./datasets/financial_phrasebank) dataset to fine-tune our model on sentiment classification on financial sentences. We will load the split `sentences_allagree`, which corresponds according to the model card to the split where there is a 100% annotator agreement.

In [ ]:
# loading dataset
dataset = load_dataset("financial_phrasebank", "sentences_allagree")
dataset = dataset["train"].train_test_split(test_size=0.1)
dataset["validation"] = dataset["test"]
del dataset["test"]

classes = dataset["train"].features["label"].names
dataset = dataset.map(
    lambda x: {"text_label": [classes[label] for label in x["label"]]},
    batched=True,
    num_proc=1,
)

Let's also apply some pre-processing of the input data, the labels needs to be pre-processed, the tokens corresponding to `pad_token_id` needs to be set to `-100` so that the `CrossEntropy` loss associated with the model will correctly ignore these tokens.

In [ ]:
# data preprocessing
text_column = "sentence"
label_column = "text_label"
max_length = 128


def preprocess_function(examples):
    inputs = examples[text_column]
    targets = examples[label_column]
    model_inputs = tokenizer(inputs, max_length=max_length, padding="max_length", truncation=True, return_tensors="pt")
    labels = tokenizer(targets, max_length=3, padding="max_length", truncation=True, return_tensors="pt")
    labels = labels["input_ids"]
    labels[labels == tokenizer.pad_token_id] = -100
    model_inputs["labels"] = labels
    return model_inputs


processed_datasets = dataset.map(
    preprocess_function,
    batched=True,
    num_proc=1,
    remove_columns=dataset["train"].column_names,
    load_from_cache_file=False,
    desc="Running tokenizer on dataset",
)

train_dataset = processed_datasets["train"]
eval_dataset = processed_datasets["validation"]

## TODO #4

위 데이터셋 로딩/가공에서 사용한 허브의 데이터셋 `financial_phrasebank` 구조와 이 셋이 어떻게 미세튜닝에 활용되었는지 개략적으로 조사하시오.
- 마크다운 스타일로 작성하시오

## 'financial_phrasebank' 데이터셋을 활용한 NLP 모델 미세 튜닝 예제

아래 코드의 개략적인 개요는 다음과 같습니다:

1. **데이터셋 로딩 및 가공**:
   - `financial_phrasebank` 데이터셋은 금융 관련 텍스트 데이터이며 Hugging Face Datasets 라이브러리를 활용합니다.
   - 데이터는 학습 및 검증 데이터셋으로 분할되고, 레이블이 처리되어 모델 학습에 맞게 준비됩니다.

2. **모델 미세 튜닝**:
   - `TrainingArguments`를 사용하여 학습 설정이 정의됩니다. 이 설정은 학습률, 배치 크기, 학습 에포크, 저장 및 평가 주기 등을 설정합니다.
   - `Trainer` 클래스를 활용하여 모델을 미세 튜닝합니다. 이때 모델, 학습 설정, 학습 데이터셋 및 검증 데이터셋이 사용됩니다.
   - `trainer.train()`을 호출하여 모델을 학습시킵니다.

3. **모델 추론**:
   - 학습이 완료된 모델을 평가하고 추론하기 위해 사용됩니다.
   - `model.eval()`을 호출하여 모델을 추론 모드로 설정하고, 입력 문장이 정의됩니다.
   - 입력 문장을 토큰화하고 모델에 전달하여 모델의 출력을 생성합니다.
   - 모델의 출력을 해독하여 예측 결과를 얻습니다.

4. **결과 출력**:
   - 입력 문장과 모델의 예측 결과가 출력됩니다.

이 코드를 통해 금융 관련 텍스트 데이터에 대한 NLP 모델을 미세 튜닝하고 이를 통해 정확한 예측을 수행하는 간단한 예제가 제시됩니다. 미세 튜닝을 통해 모델은 특정 데이터셋과 작업에 더 잘 적응할 수 있으며, 이는 더 높은 성능과 정확도를 가능하게 합니다.

## Train our model!

Let's now train our model, run the cells below.
Note that for T5 since some layers are kept in `float32` for stability purposes there is no need to call autocast on the trainer.

In [ ]:
from transformers import TrainingArguments, Trainer

training_args = TrainingArguments(
    "temp",
    evaluation_strategy="epoch",
    learning_rate=1e-3,
    gradient_accumulation_steps=1,
    auto_find_batch_size=True,
    num_train_epochs=1,
    save_steps=100,
    save_total_limit=8,
)
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=eval_dataset,
)
model.config.use_cache = False  # silence the warnings. Please re-enable for inference!

In [ ]:
trainer.train()

## Qualitatively test our model

Let's have a quick qualitative evaluation of the model, by taking a sample from the dataset that corresponds to a positive label. Run your generation similarly as you were running your model from `transformers`:

In [ ]:
model.eval()
input_text = "In January-September 2009 , the Group 's net interest income increased to EUR 112.4 mn from EUR 74.3 mn in January-September 2008 ."
inputs = tokenizer(input_text, return_tensors="pt")

outputs = model.generate(input_ids=inputs["input_ids"], max_new_tokens=10)

print("input sentence: ", input_text)
print(" output prediction: ", tokenizer.batch_decode(outputs.detach().cpu().numpy(), skip_special_tokens=True))

## TODO #5

본인의 허깅페이스 계정을 만들고 아래 허브에 업로드/다운로드/확인 과정을 본인 계정 기준으로 진행하시오.

진행 후 업르드한 허깅페이스 허브의 모델 id를 적으시오.
- 마크다운 스타일로 작성하시오.

## Share your adapters on 🤗 Hub

Once you have trained your adapter, you can easily share it on the Hub using the method `push_to_hub` . Note that only the adapter weights and config will be pushed

In [ ]:
from huggingface_hub import notebook_login

notebook_login()

In [ ]:
model.push_to_hub("yysspp/flan-t5-large-financial-phrasebank-lora", use_auth_token=True)

## Load your adapter from the Hub

You can load the model together with the adapter with few lines of code! Check the snippet below to load the adapter from the Hub and run the example evaluation!

In [ ]:
import torch
from peft import PeftModel, PeftConfig
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

peft_model_id = "yysspp/flan-t5-large-financial-phrasebank-lora"
config = PeftConfig.from_pretrained(peft_model_id)

model = AutoModelForSeq2SeqLM.from_pretrained(config.base_model_name_or_path, torch_dtype="auto", device_map="auto")
tokenizer = AutoTokenizer.from_pretrained(config.base_model_name_or_path)

# Load the Lora model
model = PeftModel.from_pretrained(model, peft_model_id)

In [ ]:
model.eval()
input_text = "In January-September 2009 , the Group 's net interest income increased to EUR 112.4 mn from EUR 74.3 mn in January-September 2008 ."
inputs = tokenizer(input_text, return_tensors="pt")

outputs = model.generate(input_ids=inputs["input_ids"], max_new_tokens=10)

print("input sentence: ", input_text)
print(" output prediction: ", tokenizer.batch_decode(outputs.detach().cpu().numpy(), skip_special_tokens=True))